# Swedish SAT example
Here we provide a usage example of the IRTorch package using a sample of data from the Swedish scholastic aptitude test (SAT). The test is used for admission to university programs and consists solely of multiple choice items. It has a quantitative and a verbal part. In this example, we will analyze the quantitative part. We will not do an in-depth analysis of the data, but rather showcase some of the main features of IRTorch to enable the user to analyze their own data.

Users are referred to the API reference section of the documentation for more detailed information of different functions and classes. Note that the results might vary slightly from those presented here due to randomness in the optimization algorithm, as well as differences in the computing hardware (CPU or GPU), the operating system, and the versions of the packages used.

## Load the libraries
We start by loading the libraries and modules that we will use for this example.

In [9]:
import torch
from irtorch.models import NominalResponse, MonotoneNN
from irtorch.estimation_algorithms import AE
from irtorch.load_dataset import swedish_sat_quantitative
from irtorch.cross_validation import cross_validation
from irtorch.utils import impute_missing, split_data

<div class="hidden-input">

In [10]:
import plotly
plotly.offline.init_notebook_mode() 

</div>

## The test data
The package requires the data to be in a PyTorch tensor with test takers as rows and items as columns. For an example on how to convert a pandas dataframe to a PyTorch tensor, check out the [National Mathematics example](./national_mathematics.ipynb).

In this example, we will load the data directly from within the package. We will model not just the correct and incorrect item responses, but also the individual distractor response options for each test item. The possible item responses should be coded 0, 1, ... and missing responses coded as nan or -1. For multiple choice data, we also need a list containing the correct response options for the items. Each list element should correspond to one item. Note that for a 4 option item, the responses are coded 0, 1, 2, 3, but the correct response is indexed from 1, and thus if the first option is correct, the first element in the list should be 1. Below we read both the item responses and the correct response options directly from the package.

In [11]:
data_sat, correct_responses = swedish_sat_quantitative()

For the sake of this example, we will simplify things and set missing item responses to a random incorrect response option using the `impute_missing` function. In practice, missing responses should be handled more carefully.

In [12]:
data_sat = impute_missing(data_sat, correct_responses)

## Initializing models
We start by initializing two IRT models using our data and the list of correct responses. A nominal response (NR) model and a more flexible Monotone Multiple Choice Neural Network (MMCNN) model. For more details on these IRT models and other available models, see the [IRT Models](./../irt_models.rst) section.

In [13]:
torch.manual_seed(42)
nr = NominalResponse(data=data_sat, mc_correct=correct_responses)
torch.manual_seed(42)
mmcnn = MonotoneNN(data = data_sat, mc_correct=correct_responses)

## Fitting the models
We recommend splitting your test data into a training and a test set to ensure we are not overfitting the model to the test data. 

In [14]:
torch.manual_seed(4)
train_data, test_data = split_data(data_sat, 0.8)

Each model can now be fit using the `fit()` instance method. `fit()` requires the model training data as a tensor, as well as an instance of the fitting algorithm. The [Estimation algorithms](./../estimation_algorithms.rst) section contains all available fitting algorithms. Here we will use Autoencoders (AEs) to fit the models.

Note that since this is a quite large dataset with 5000 test takers, fitting can take some time. Because of this, it can be useful to save the parameters of the fitted model to disk for later use using `save_model()` with the filename of choice.

Fitting will be done using the GPU if available, otherwise the CPU will be used. This can also be specified using the `device` argument, i.e. `nr.fit(train_data=train_data, algorithm=AE(), device = "cpu")`.

In [15]:
nr.fit(train_data=train_data, algorithm=AE())
nr.save_model("swesat_nr.pt")

Epoch: 50. Average training batch loss function: 77.7772 

INFO: Stopping training after 5 learning rate updates.
INFO: Best model found at epoch 46 with loss 77.7147.


In [16]:
mmcnn.fit(train_data=train_data, algorithm=AE())
mmcnn.save_model("swesat_mmcnn.pt")

Epoch: 52. Average training batch loss function: 77.4746 

INFO: Stopping training after 5 learning rate updates.
INFO: Best model found at epoch 46 with loss 77.3970.


We can load the saved model parameters to a new `IRT` class instance using `load_model()`. Note that the instance needs to be created in the same way as for the original model for `load_model()` to work.

In [17]:
nr = NominalResponse(data=data_sat, mc_correct=correct_responses)
mmcnn = MonotoneNN(data=data_sat, mc_correct=correct_responses)
nr.load_model("swesat_nr.pt")
mmcnn.load_model("swesat_mmcnn.pt")

The `plotting` property of our models contains methods for visualization. We appear to have converged to a good solution as not much improvement or fluctuation is shown in the later 30 epochs. See [Plotting](./../plotting.rst) for details on the available plots.

In [18]:
nr.plotting.plot_training_history().show()
mmcnn.plotting.plot_training_history().show()

## Estimation of latent traits
We can estimate the latent trait scores of the test takers using the `latent_scores()` method. In addition to traditional methods such as Maximum Likelihood (ML), autoencoder models give the option to use encoder neural network (NN) to estimate the latent traits. The ML method results in a better fit to the data in terms of the likelihood, but for large datasets the NN method is much faster. We will use the NN method in this example.

In [19]:
theta_scores_train_nr = nr.latent_scores(train_data, theta_estimation="NN")
theta_scores_train_mmcnn = mmcnn.latent_scores(train_data, theta_estimation="NN")
theta_scores_test_nr = nr.latent_scores(test_data, theta_estimation="NN")
theta_scores_test_mmcnn = mmcnn.latent_scores(test_data, theta_estimation="NN")

INFO: NN estimation of theta scores.
INFO: NN estimation of theta scores.
INFO: NN estimation of theta scores.
INFO: NN estimation of theta scores.


We can plot the latent trait distributions from each model to get an overview of the test takers' abilities. Since autoencoder models make no assumptions about the distribution of the latent traits, these distribution will not be normal, and we have skewed distributions for both models.

In [20]:
nr.plotting.plot_latent_score_distribution(theta_scores_train_nr).show()
mmcnn.plotting.plot_latent_score_distribution(theta_scores_train_mmcnn).show()

For these AE fitted models, we suggest converting the latent trait scales to bit scales instead. Bit scales are ratio scales, and make scores from different models comparable as long as they are fitted to the same test data. We can compute the bit scores using the `scale` argument.

In [21]:
bit_scores_train_nr, _ = nr.bit_scales.bit_scores_from_theta(theta_scores_train_nr, theta_estimation="NN")
bit_scores_train_mmcnn, _ = mmcnn.bit_scales.bit_scores_from_theta(theta_scores_train_mmcnn, theta_estimation="NN")
bit_scores_test_nr, _ = nr.bit_scales.bit_scores_from_theta(theta_scores_test_nr, theta_estimation="NN")
bit_scores_test_mmcnn, _ = mmcnn.bit_scales.bit_scores_from_theta(theta_scores_test_mmcnn, theta_estimation="NN")

INFO: Using traning data theta scores as population theta scores for bit score computation.
INFO: Approximating minimum bit score theta from random guessing data for latent variable 1.
INFO: NN estimation of theta scores.
INFO: Using traning data theta scores as population theta scores for bit score computation.
INFO: Approximating minimum bit score theta from random guessing data for latent variable 1.
INFO: NN estimation of theta scores.
INFO: Using traning data theta scores as population theta scores for bit score computation.
INFO: Approximating minimum bit score theta from random guessing data for latent variable 1.
INFO: NN estimation of theta scores.
INFO: Using traning data theta scores as population theta scores for bit score computation.
INFO: Approximating minimum bit score theta from random guessing data for latent variable 1.
INFO: NN estimation of theta scores.


If we plot the bit score distribution for each model, we can see that they are much more similar compared to the distributions of the original latent variables.

In [22]:
nr.plotting.plot_latent_score_distribution(bit_scores_train_nr).show()
mmcnn.plotting.plot_latent_score_distribution(bit_scores_train_mmcnn).show()

## Item response functions
To visualize item response functions, we use the `plot_item_probabilities()` method. Here we plot the curves for item 27 on the bit scale. We can see that the probability of answering the item correctly (Option 1) increases with the latent trait score. By far the most common distractor response is option 3, especially at the lower end of the ability scale.

In [23]:
nr.plotting.plot_item_probabilities(item = 27, scale = "bit", theta_estimation="NN").show()
mmcnn.plotting.plot_item_probabilities(item = 27, scale = "bit", theta_estimation="NN").show()

INFO: Using traning data theta scores as population theta scores for bit score computation.
INFO: Approximating minimum bit score theta from random guessing data for latent variable 1.
INFO: NN estimation of theta scores.


INFO: Using traning data theta scores as population theta scores for bit score computation.
INFO: Approximating minimum bit score theta from random guessing data for latent variable 1.
INFO: NN estimation of theta scores.


## Item parameters
For parametric IRT models such as the NR model, we can get the estimated item parameters using the `item_parameters()` method. We use the `irt_format` argument to specify that we want to return the item parameters in traditional IRT format (and not as slopes and intercepts). We have a slope (a) and a threshold (b) for each item response option. Note that many items have 4 instead of 5 response options. For these items the a and b values for the last option are not used and shown as 0 in the output.

In [24]:
nr.item_parameters(irt_format=True)

a11       a12       a13       a14  a15        b1        b2        b3  \
0   1.691483  1.330251  0.456448  1.259319  0.0  2.162338  2.075619 -0.593106   
1   0.471060  1.720327  1.824823  0.242134  0.0  0.004748  2.444875  4.703164   
2   0.897379  0.483734  1.449305  1.593523  0.0  0.910921 -0.432191  0.079861   
3   1.053998  1.599175  0.448527  1.437635  0.0 -0.114090  1.322356 -0.470380   
4   1.188216  0.543242  1.321855  1.141007  0.0  0.657611 -0.396963  1.012175   
..       ...       ...       ...       ...  ...       ...       ...       ...   
75  0.870744  0.724149  1.149154  1.244932  0.0  0.273775 -0.519123  0.513229   
76  0.993095  0.680227  1.298334  1.335998  0.0 -0.317700 -0.514360  0.249091   
77  0.699961  1.145239  1.253215  1.342542  0.0 -0.769122 -0.116423  1.253589   
78  1.249384  1.156503  1.159056  0.736832  0.0  1.223540 -0.273263  0.514744   
79  0.719014  1.146049  1.118424  1.106061  0.0 -0.275437  0.501810  0.211794   

          b4   b5  
0   0.582729 -0.0  
1  -0.398004 -0.0  
2   1.203460 -0.0  
3   2.197065 -0.0  
4   0.565197 -0.0  
..       ...  ...  
75  1.217309 -0.0  
76  1.441181 -0.0  
77  1.895372 -0.0  
78 -0.536695 -0.0  
79  0.222891 -0.0  

[80 rows x 10 columns]

## Evaluate the model fit
There are various ways to evaluate which model fits the data best and many are available within the `evaluation` model property (see the [Model evaluation](./../evaluation.rst) section). We can compare the log-likelihood of each model on our test data, the predictive accuracy, different types of residuals or infit and outfit statistics.

Starting with log-likelihood. A larger log-likelihood indicates a better fit. We see that in this case, the MMCNN model fits the data better than the NR model.

In [25]:
print(nr.evaluation.log_likelihood(data=test_data, theta=theta_scores_test_nr))
print(mmcnn.evaluation.log_likelihood(data=test_data, theta=theta_scores_test_mmcnn))

tensor(-78095.1406)
tensor(-78018.2656)


Predictive accuracy of each model on our test data can be computed using the `accuracy()` instance method. This method returns the proportion of correctly predicted item responses. We see that the MMCNN model has a slightly better predictive accuracy than the NR model, but the difference is very small in this case.

In [26]:
print(nr.evaluation.accuracy(data=test_data, theta=theta_scores_test_nr))
print(mmcnn.evaluation.accuracy(data=test_data, theta=theta_scores_test_mmcnn))

tensor(0.5943)
tensor(0.5966)


We can also add grouped residuals to our item response function figures to visualize model fit. For these figures, the test takers are divided into groups based on their latent trait scores. Within each group, the proportion of test takers responding with each response option is plotted and compared to the proportion expected by the model. Thus, a good overlap of the data and model dots in the figures indicate a good fit. Both models provide a good fit to the data for most items on this test with some exceptions. For item 27, the NR model struggles a bit with the third and fifth response options compared to the MMCNN model.

In [27]:
nr.plotting.plot_item_probabilities(item = 27, scale = "bit", plot_group_fit=True, theta_estimation="NN").show()
mmcnn.plotting.plot_item_probabilities(item = 27, scale = "bit", plot_group_fit=True, theta_estimation="NN").show()

INFO: Using traning data theta scores as population theta scores for bit score computation.
INFO: Approximating minimum bit score theta from random guessing data for latent variable 1.
INFO: NN estimation of theta scores.
INFO: NN estimation of theta scores.
INFO: Using traning data theta scores as population theta scores for bit score computation.
INFO: Approximating minimum bit score theta from random guessing data for latent variable 1.
INFO: NN estimation of theta scores.


INFO: Using traning data theta scores as population theta scores for bit score computation.
INFO: Approximating minimum bit score theta from random guessing data for latent variable 1.
INFO: NN estimation of theta scores.
INFO: NN estimation of theta scores.
INFO: Using traning data theta scores as population theta scores for bit score computation.
INFO: Approximating minimum bit score theta from random guessing data for latent variable 1.
INFO: NN estimation of theta scores.


Infit and outfit statistics can be computed using the `infit_outfit()` method for both items and respndents. These statistics are traditional fit statistics in IRT and are typically computed on the training data. Here we compute both statistics for each item with the `level="item"` argument.

In [28]:
infit_item_nr, outfit_item_nr = nr.evaluation.infit_outfit(data=train_data, theta=theta_scores_train_nr, level="item")
infit_item_mmcnn, outfit_item_mmcnn = mmcnn.evaluation.infit_outfit(data=train_data, theta=theta_scores_train_mmcnn, level="item")

Infit and outfit are based on the residuals, and a value of 1 indicates a perfect fit. Values significantly greater than 1 indicate misfit, with higher values suggesting responses were less predictable than expected (possibly due to guessing, cheating, or misunderstanding). Values significantly less than 1 suggest overfit, where responses are too predictable, indicating possible redundancy among items or that the items are not contributing additional useful information about the construct being measured. Below we see that are infit and outfit statistics stay close to one for both models, indicating good fit.

In [29]:
print(f"NR infit: {infit_item_nr}")
print(f"MMCNN infit: {infit_item_mmcnn}")
print(f"NR outfit: {outfit_item_nr}")
print(f"MMCNN outfit: {outfit_item_mmcnn}")

NR infit: tensor([0.9835, 0.9704, 0.9890, 0.9878, 1.0019, 0.9751, 1.0010, 1.0048, 0.9895,
        1.0037, 0.9954, 1.0059, 0.9994, 0.9686, 0.9896, 0.9934, 0.9960, 1.0007,
        1.0065, 0.9942, 0.9875, 0.9867, 0.9777, 0.9924, 0.9865, 0.9940, 0.9938,
        1.0008, 1.0014, 1.0014, 1.0014, 1.0062, 1.0004, 1.0016, 1.0043, 1.0069,
        1.0061, 1.0037, 1.0023, 0.9988, 0.9490, 0.9859, 0.9986, 1.0026, 0.9633,
        0.9930, 0.9943, 0.9978, 0.9981, 0.9823, 1.0012, 0.9891, 0.9945, 0.9932,
        0.9907, 0.9946, 0.9795, 0.9957, 0.9953, 0.9971, 0.9992, 0.9938, 0.9739,
        1.0065, 1.0114, 0.9931, 1.0002, 0.9920, 0.9961, 1.0067, 1.0017, 0.9999,
        1.0123, 0.9989, 0.9972, 0.9949, 1.0127, 1.0014, 1.0029, 1.0022])
MMCNN infit: tensor([1.0071, 1.0248, 1.0112, 0.9922, 1.0116, 0.9982, 0.9858, 0.9987, 1.0260,
        1.0187, 0.9878, 1.0261, 1.0159, 1.0131, 1.0408, 1.0195, 0.9996, 1.0084,
        1.0105, 1.0036, 1.0006, 1.0131, 0.9903, 1.0109, 1.0112, 1.0141, 0.9952,
        1.0142, 1.0121, 

## Information


We can plot the Fisher information using the `plot_information()` method for both individual items and the test as a whole. As for test information, we see that the MMCNN model suggests more information closer to 0 compared to the NR model. Both models suggest that the test provides the most information for test takers with bit scores below 20. Note that this is also were most test takers are located (from the density plots from before).

In [30]:
nr.plotting.plot_information(scale="bit", theta_estimation="NN").show()
mmcnn.plotting.plot_information(scale="bit", theta_estimation="NN").show()

INFO: Using traning data theta scores as population theta scores for bit score computation.
INFO: Approximating minimum bit score theta from random guessing data for latent variable 1.
INFO: NN estimation of theta scores.
INFO: Computing Jacobian for all items and item categories...
INFO: Using traning data theta scores as population theta scores for bit score computation.
INFO: Using traning data theta scores as population theta scores for bit score computation.


INFO: Using traning data theta scores as population theta scores for bit score computation.
INFO: Approximating minimum bit score theta from random guessing data for latent variable 1.
INFO: NN estimation of theta scores.
INFO: Computing Jacobian for all items and item categories...
INFO: Using traning data theta scores as population theta scores for bit score computation.
INFO: Using traning data theta scores as population theta scores for bit score computation.


## Cross validation

If we want to optimize the hyperparameters for a model, we can use the `cross_validation()` method from the `cross_validaton` module. In the example below, we optimize the learning rate and the batch size for the MMCNN model. A dictionary of hyperparameters should be specified with the `params_grid` argument. The method runs 5-fold cross validation for all possible parameter combinations in the `params_grid` dictionary.

When `device="cpu"`, the method runs on multiple CPU cores using the `multiprocessing` package. For details on why we need the `if __name__ == "__main__":` line, see the [multiprocessing documentation](https://docs.python.org/3/library/multiprocessing.html). 

In [31]:
torch.manual_seed(42)
mmcnn_cv = NominalResponse(data=train_data)
params_grid = {
    "learning_rate": [0.05, 0.1],
    "batch_size": [64, 128],
}
if __name__ == "__main__":
    cv_result = cross_validation(mmcnn_cv, data = train_data, folds = 5, params_grid = params_grid, theta_estimation="NN", device="cpu", algorithm=AE())

print(cv_result)
print(f"--------------------\nBest hyperparameters\n--------------------")
best_params = cv_result.loc[cv_result["log_likelihood"].idxmax(), ["learning_rate", "batch_size"]]
print(f"learning rate: {best_params['learning_rate']}\nbatch size: {best_params['batch_size']}")

INFO: Performing cross-validation with 4 parameter combinations


Using 24 cores
   learning_rate  batch_size  log_likelihood
0           0.05          64   -62206.323438
1           0.05         128   -62203.978906
2           0.10          64   -62199.372656
3           0.10         128   -62204.569531
--------------------
Best hyperparameters
--------------------
learning rate: 0.1
batch size: 64.0


Once we have the results, we can fit the model using the full training data with the best set of hyperparameters.

In [32]:
mmcnn_cv.fit(train_data, algorithm=AE(), learning_rate=best_params["learning_rate"], batch_size=int(best_params["batch_size"]))

Epoch: 56. Average training batch loss function: 77.7561 

INFO: Stopping training after 5 learning rate updates.
INFO: Best model found at epoch 56 with loss 77.7561.
